In [4]:
from dash import Dash, dcc, html, Input, Output
import plotly.express as px
import plotly.graph_objects as go
import pandas as pd
import numpy as np
from urllib.request import urlopen
import json

In [5]:
hotness = pd.read_csv('data/rdchotness.csv')
print(hotness.columns)

hotness_grouped = hotness[hotness['MSA'] == 'Dayton, OH'].groupby(['zip_code', 'year_month'])['median_listing_price'].agg('median').reset_index()
hotness_grouped.describe

Index(['month_date_yyyymm', 'postal_code', 'zip_name', 'nielsen_hh_rank',
       'hotness_rank', 'hotness_rank_mm', 'hotness_rank_yy', 'hotness_score',
       'supply_score', 'demand_score', 'median_days_on_market',
       'median_days_on_market_mm', 'median_dom_mm_day',
       'median_days_on_market_yy', 'median_dom_yy_day', 'median_dom_vs_us',
       'ldp_unique_viewers_per_property_mm',
       'ldp_unique_viewers_per_property_yy',
       'ldp_unique_viewers_per_property_vs_us', 'median_listing_price',
       'median_listing_price_mm', 'median_listing_price_yy',
       'median_listing_price_vs_us', 'quality_flag'],
      dtype='object')


KeyError: 'MSA'

In [ ]:

fig = go.Figure()

for i in hotness_grouped['zip_code']:
    zip = i
    fig.add_trace(go.Scatter(x=hotness_grouped['year_month'], y=hotness_grouped[hotness_grouped['zip_code'] == i]['median_listing_price'], name=zip,
                         line=dict(color='#B5B6B7', width=2)))

fig.update_xaxes(type='category')
fig.update_xaxes(categoryorder='category ascending')

fig.show()



In [ ]:
fig = px.line(hotness_grouped, x='year_month', y='median_listing_price', color='zip_code')

fig.update_xaxes(type='category')
fig.update_xaxes(categoryorder='category ascending')

for i in fig['data']:
    i['line']['color'] = '#B5B6B7'
    i['line']['width'] = 2

fig['data'][['legendgroup'] == '45432']['line']['color'] = '#EB5AEB'
fig['data'][['legendgroup'] == '45432']['line']['width'] = 3
fig.show()

In [ ]:
hotness_grouped['zip_code'].dtype

dtype('int64')

In [5]:
core = pd.read_csv('data/rdc_core.csv')
state_files = pd.read_csv('data/state_files.csv').set_index('State')

selected_msa = 'Chicago-Naperville-Joliet, IL-IN-WI'
states = []

df = core[core['MSA'] == selected_msa]

for i in df['State'].unique():
    states.append(i)

selected_states = pd.DataFrame(states)
selected_states = selected_states.set_index(0, drop=True).join(state_files, how='left')

print(selected_states)

                             state_json
0                                      
IN    in_indiana_zip_codes_geo.min.json
WI  wi_wisconsin_zip_codes_geo.min.json
IL   il_illinois_zip_codes_geo.min.json


In [36]:
state_zips = []
for state in selected_states['state_json']:
    with urlopen(f'https://raw.githubusercontent.com/OpenDataDE/State-zip-code-GeoJSON/master/{state}') as response:
        state_zips.append(json.load(response))


( 39.9083827 ,  -86.2347427 )


In [ ]:
fig = go.Figure(layout_height=600)
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})

for i in state_zips:
    fig.add_trace(go.Choropleth(geojson=i,
                    locations=df['zip_num'], 
                    z=df['median_listing_price'],
                    featureidkey='properties.ZCTA5CE10',
                    colorscale = 'Reds'))

fig.update_geos(fitbounds='locations', visible=False)
fig.show()

In [11]:
print(fig['data'][0]['geojson']['features']['geometry']['coordinates'])

TypeError: list indices must be integers or slices, not str

In [38]:
coords = pd.DataFrame({'lat': [], 'lon': []})

for i in state_zips:

    lats = [i['features'][j]['properties']['INTPTLAT10'] for j in range(1, len(i['features']))]
    lons = [i['features'][j]['properties']['INTPTLON10'] for j in range(1, len(i['features']))]

    latlon = pd.DataFrame({'lat': lats, 'lon': lons})
    latlon['lat'] = latlon['lat'].apply(float)
    latlon['lon'] = latlon['lon'].apply(float)

    coords.append(latlon)

print(latlon)

            lat        lon
0     40.120548 -91.434891
1     39.707353 -91.024237
2     39.796403 -91.165124
3     38.890364 -89.427497
4     38.940678 -89.282715
...         ...        ...
1378  41.443615 -87.708354
1379  37.817138 -89.030678
1380  37.801912 -89.084262
1381  37.783608 -89.119606
1382  42.268117 -89.262692

[1383 rows x 2 columns]


C:\Users\TylerFrankenberg\AppData\Local\Temp\ipykernel_46164\1683942819.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  coords.append(latlon)
